In [2]:
import re
import json
import spacy
from nltk.tree import Tree
from nltk.tree import ParentedTree
from stanfordcorenlp import StanfordCoreNLP


# to start a CoreNLP Server, please download the stanford-corenlp-full file and run the
# "java -mx4g -cp "*" edu.stanford.nlp.pipeline.StanfordCoreNLPServer -port 9000 -timeout 15000" 
# in the command line
stanf_nlp = StanfordCoreNLP('http://localhost', port=9000)
spacy_nlp = spacy.load('en_core_web_sm')

documents = json.load(open('documents.json','r'))

def set_custom_boundaries(doc):
    for token in doc[:-1]:
        if token.text == ':':
            doc[token.i+1].is_sent_start = False
    return doc

spacy_nlp.add_pipe(set_custom_boundaries, before = 'parser')


In [3]:
import json
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import time
import numpy as np
from tqdm import tqdm
import spacy


def build_vector():
    vector = {}
    tfidf = {}
    sent_set = {}
    for doc_id in tqdm(range(len(documents))):
        sentence_list = []
        for para in documents[doc_id].get('text'):
            for sent in spacy_nlp(para).sents:
                sentence_list.append(sent.text)
            
        vector[doc_id] = TfidfVectorizer(stop_words=stopwords.words('english'),ngram_range=(1, 2))
        tfidf[doc_id] = np.array(vector[doc_id].fit_transform(sentence_list).toarray())
        sent_set[doc_id] = sentence_list
    return vector, tfidf, sent_set

def convert_query_vect(query, vectorizer):
    return np.array(vectorizer.transform(query).toarray())


vect, tfidf, sent = build_vector()


100%|██████████| 441/441 [07:13<00:00,  1.02it/s]


In [4]:
def rank_sent(doc_vect, query_vect):
    cosSimDict = {}
    for i in range(doc_vect.shape[0]):
        similarity = cosine_similarity(doc_vect[i].reshape(1,-1), query_vect[0].reshape(1,-1))
        cosSimDict[i] = similarity[0][0]
    newCosSimDict = [doc_ID for doc_ID in sorted(cosSimDict, key=cosSimDict.get, reverse=True)]
    
    return newCosSimDict[:10]

train = json.load(open('training.json', 'r'))
import re
def check_acc(sent_list, answer):
    for sent in sent_list:
        if answer in sent:
            return True
    return False

In [5]:
import string
from nltk.tree import Tree
from nltk.tree import ParentedTree
from stanfordcorenlp import StanfordCoreNLP

stanf_nlp = StanfordCoreNLP('http://localhost', port=9000)

fixed_stopwords = ['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're",
                   "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he',
                   'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's",
                   'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'this', 'that',
                   "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being',
                   'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and',
                   'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with',
                   'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above',
                   'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again',
                   'further', 'then', 'once', 'here', 'there', 'all', 'any', 'both', 'each', 'few', 'more',
                   'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than',
                   'too', 'very', 's', 't', 'can', 'will', 'just', 'don', "don't", 'should', "should've",
                   'now', 'd', 'll', 'm', 'o', 're', 've', 'y', 'ain', 'aren', "aren't", 'couldn', "couldn't",
                   'didn', "didn't", 'doesn', "doesn't", 'hadn', "hadn't", 'hasn', "hasn't", 'haven', "haven't",
                   'isn', "isn't", 'ma', 'mightn', "mightn't", 'mustn', "mustn't", 'needn', "needn't", 'shan',
                   "shan't", 'shouldn', "shouldn't", 'wasn', "wasn't", 'weren', "weren't", 'won', "won't", 
                   'wouldn', "wouldn't"]

question_words = ['what', 'when', 'where', 'who', 'how', 'whose', 'whom', 'which', 'why']


def question_type(question):
    wh_word = ""
    wh_tri_gram = []
    question_word = ""
    new_tokens = []
    keyword = ''

    before_doc = spacy_nlp(u'' + question)
    count = 0
    for token in before_doc:
        if token.text.lower() in question_words:
            count += 1
    
    if count > 1:
        r_parsed= stanf_nlp.parse(question)
        r_tree = ParentedTree.fromstring(r_parsed)

        before = []
        for node in r_tree.pos():
            word, pos = node
            before.append(word)

        p_tree = None
        for subtree in r_tree.subtrees():
            if subtree.label() == 'SBAR':
                p_tree = subtree
                break

        if p_tree:
            after = []
            for node in p_tree.pos():
                word, pos = node
                after.append(word)

            if after[0] == before[0]:
                final = before[len(after):]
            else:
                final = []
                for w in range(len(before)):
                    if after[0] == before[w]:
                        break
                    else:
                        final.append(before[w])

            flag = False
            for w in final:
                if w in question_words:
                    flag = True
                    break

            if flag == True:
                cleaned_query = " ".join(final)
            else:
                cleaned_query = question
        else:
            cleaned_query = question
    else:
        cleaned_query = question
            
    
    query_doc = spacy_nlp(u'' + cleaned_query)
    lemma = [token.lemma_ for token in query_doc if token.lemma_ != '-PRON-']
    meaningful_words = [token for token in lemma if token not in fixed_stopwords]
    for i in range(len(meaningful_words)):
        if meaningful_words[i] in question_words and i != 0:
            if meaningful_words[i-1] in string.punctuation:
                meaningful_words = meaningful_words[i:]
                break
        else:
            break
    non_binary = False
    for t in meaningful_words:
        if t in question_words:
            non_binary = True
    
    if non_binary:
        if meaningful_words[0] in question_words:
            meaningful_words = [token for token in meaningful_words if token not in string.punctuation]
            if len(meaningful_words) > 2:
                raw_text = ' '.join(meaningful_words)
                new_doc = spacy_nlp(u'' + raw_text)
                for token in new_doc:
                    if token.text in question_words:
                        wh_word = token.text
                        wh_tri_gram.append(token.text)
                        wh_tri_gram.append(str(new_doc[token.i + 1]))
                        wh_tri_gram.append(str(new_doc[token.i + 2]))
                        flag = True
                        break

            else:
                raw_text = ' '.join(meaningful_words)
                new_doc = spacy_nlp(u'' + raw_text)
                for token in new_doc:
                    if token.text in question_words:
                        wh_word = token.text
                        wh_tri_gram.append(token.text)
                        wh_tri_gram.append(str(new_doc[token.i + 1]))
                        wh_tri_gram.append(str(new_doc[token.i + 1]))
        elif meaningful_words[-2] in question_words:
            meaningful_words = [token for token in meaningful_words if token not in string.punctuation]
            if len(meaningful_words) > 2:
                raw_text = ' '.join(meaningful_words)
                new_doc = spacy_nlp(u'' + raw_text)
                for token in new_doc:
                    if token.text in question_words:
                        wh_word = token.text
                        wh_tri_gram.append(token.text)
                        wh_tri_gram.append(str(new_doc[token.i - 1]))
                        wh_tri_gram.append(str(new_doc[token.i - 2]))
            else:
                raw_text = ' '.join(meaningful_words)
                new_doc = spacy_nlp(u'' + raw_text)
                for token in new_doc:
                    if token.text in question_words:
                        wh_word = token.text
                        wh_tri_gram.append(token.text)
                        wh_tri_gram.append(str(new_doc[token.i - 1]))
                        wh_tri_gram.append(str(new_doc[token.i - 1]))
        else:
            raw_doc = spacy_nlp(u'' + cleaned_query)
            raw_lemma = [token.lemma_ for token in raw_doc if token.lemma_ != '-PRON-' and token.text not in string.punctuation]
            raw_text = ' '.join(raw_lemma)
            new_doc = spacy_nlp(u'' + raw_text)
            index = 0
            for token in new_doc:
                if token.text in question_words:
                    wh_word = token.text
                    wh_tri_gram.append(token.text)
                    break
                index += 1
            raw_meaningful_words = [token.text for token in new_doc if token.text not in stopwords.words("english")]
            raw_meaningful_dict = {}
            for i in range(len(raw_lemma)):
                for w in raw_meaningful_words:
                    if w == raw_lemma[i]:
                        raw_meaningful_dict[w] = i
            raw_meaningful_dict1 = {}
            for k,v in raw_meaningful_dict.items():
                raw_meaningful_dict1[k] = v - index
        
            sub_dict1 = {}
            sub_dict2 = {}
            for k,v in raw_meaningful_dict1.items():
                if v > 0:
                    sub_dict1[k] = v
                else:
                    sub_dict2[k] = v
            
            sub_dict3 = sorted(sub_dict1.items(), key=lambda item:item[1])
            sub_dict4 = sorted(sub_dict2.items(), key=lambda item:item[1], reverse=True)
            
            if len(sub_dict3) >= 2:
                wh_tri_gram.append(sub_dict3[0][0])
                wh_tri_gram.append(sub_dict3[1][0])
            elif len(sub_dict3) == 1:
                if len(sub_dict4) >= 1:
                    wh_tri_gram.append(sub_dict3[0][0])
                    wh_tri_gram.append(sub_dict4[0][0])
                else:
                    wh_tri_gram.append(sub_dict3[0][0])
                    wh_tri_gram.append(sub_dict3[0][0])
    else:
        meaningful_words = [token for token in meaningful_words if token not in string.punctuation]
        wh_tri_gram.append(meaningful_words[0])
        wh_tri_gram.append(meaningful_words[1])
        wh_tri_gram.append(meaningful_words[2])
    
    return wh_tri_gram

In [6]:
num_words = ['number', 'percentage', 'age', 'price', 'many', 'much', 'long', 'far', 
             'large', 'big', 'often', 'fast', 'close', 'old', 'light', 'value']
loc_words = ['location', 'city', 'country', 'state', 'place', 'town','river', 'bridge', 'building']
time_words = ['year', 'month', 'day', 'date', 'time', 'hour', 'hours', 'period']
person_words = ['person', 'people']

def query_type(q_chunk):
    if q_chunk[0] == 'when':
        q_type = 'when'
    elif q_chunk[0] == 'who':
        q_type = 'who'
    elif q_chunk[0] == 'where':
        q_type = 'where'
    elif q_chunk[0] == 'whose':
        q_type = 'who'
    elif q_chunk[0] == 'whom':
        q_type = 'who'
    elif q_chunk[0] == 'why':
        q_type = 'desc'
    elif q_chunk[0] == 'how':
        if q_chunk[1] in num_words:
            q_type = 'num'
        else:
            q_type = 'desc'
    elif q_chunk[0] == 'which':
        if q_chunk[1] in loc_words:
            q_type = 'where'
        elif q_chunk[1] in num_words:
            q_type = 'num'
        elif q_chunk[1] in person_words:
            q_type = 'who'
        elif q_chunk[1] in time_words:
            q_type = 'when'
        else:
            q_type = 'desc'
    elif q_chunk[0] == 'what':
        if q_chunk[1] in time_words:
            q_type = 'when'
        elif q_chunk[1] in person_words:
            q_type = 'who'
        elif q_chunk[1] in loc_words:
            q_type = 'where'
        elif q_chunk[1] in num_words:
            q_type = 'num'
        else:
            q_type = 'desc'
    else:
        q_type = 'binary'
    return q_type


In [7]:
def check_when(label):
    if label=="DATE" or label == "TIME":
        return True
    else:
        return False

def check_who(label):
    if label == "PERSON" or label == "ORG" or label == "NORP" or label == "PRODUCT":
        return True
    else:
        return False
    
def check_where(label):
    if label=="GPE" or label == "ORG"or label == "LOC"or label == "FAC":
        return True
    else:
        return False

def check_num(label):
    if label=="PERCENT" or label == "MONEY"or label == "CARDINAL" or label == "QUANTITY" :
        return True
    else:
        return False
    
def find_answer(nlp_sent, token, ans, que_type):
    if que_type == "num":
        if check_num(token.ent_type_):
            ans += " {}".format(token.text)
    if que_type == "when":
        if check_when(token.ent_type_):
            ans += " {}".format(token.text)
    if que_type == "who":
        if check_who(token.ent_type_):
            ans += " {}".format(token.text)
    if que_type == "where":
        if check_where(token.ent_type_):
            ans += " {}".format(token.text)
    if que_type == "desc":
        ans += " {}".format(token.text)
    for word in token.children:
        ans += find_answer(nlp_sent, word, ans, que_type)
    return ans

In [8]:
def extract_answer(question, root_word, sentence, que_type):

    spacy_nlp_sent = spacy_nlp(sentence)
    
    candidate_ans = ""
    if que_type=="when":
        for token in spacy_nlp_sent:
            if token.lemma_ == root_word:
                for cand in [child for child in token.children]:
                    if check_when(cand.ent_type_):
                        candidate_ans +=" "+ str(cand.text)
                        for c in cand.children:
                            if check_when(cand.ent_type_):
                                candidate_ans +=" "+ str(c.text)
                    elif cand.dep_ == "prep":
                        for c in cand.children:
                            if check_when(c.ent_type_):
                                candidate_ans +=" "+ str(c.text)
        if candidate_ans == "":
            for token in spacy_nlp_sent.ents:
                if check_when(token.label_):
                    candidate_ans += " "+str(token.text)
        if candidate_ans == "":
            for chunk in spacy_nlp_sent.noun_chunks:
                candidate_ans +=" "+ str(chunk.text)
                    
    if que_type=="who":
        for token in spacy_nlp_sent:
            if token.lemma_ == root_word:
                for cand in [child for child in token.children]:
                    if check_who(cand.ent_type_):
                        candidate_ans +=" "+ str(cand.text)
                        for c in cand.children:
                            if check_who(cand.ent_type_):
                                candidate_ans +=" "+ str(c.text)
                    elif cand.dep_ == "prep":
                        for c in cand.children:
                            if check_who(c.ent_type_):
                                candidate_ans +=" "+ str(c.text)
                    elif cand.dep_ == "nsubjpass" or cand.dep_ == "nsubj":
                        for chunk in spacy_nlp_sent.noun_chunks:
                            if chunk.root.text == cand.text:
                                candidate_ans +=" "+ str(chunk.text)
        if candidate_ans == "":
            for token in spacy_nlp_sent.ents:
                if check_who(token.label_):
                    candidate_ans += " "+str(token.text)
        if candidate_ans == "":
            for chunk in spacy_nlp_sent.noun_chunks:
                candidate_ans +=" "+ str(chunk.text)

    if que_type=="where":
        for token in spacy_nlp_sent:
            if token.lemma_ == root_word:
                for cand in [child for child in token.children]:
                    if check_where(cand.ent_type_):
                        candidate_ans +=" "+ str(cand.text)
                        for c in cand.children:
                            if check_where(cand.ent_type_):
                                candidate_ans +=" "+ str(c.text)
                    elif cand.dep_ == "prep":
                        for c in cand.children:
                            if check_where(c.ent_type_):
                                candidate_ans +=" "+ str(c.text)
                    elif cand.dep_ == "nsubjpass" or cand.dep_ == "nsubj":
                        for chunk in spacy_nlp_sent.noun_chunks:
                            if chunk.root.text == cand.text:
                                candidate_ans +=" "+ str(chunk.text)
        if candidate_ans == "":
            for token in spacy_nlp_sent.ents:
                if check_where(token.label_):
                    candidate_ans += " "+str(token.text)
        if candidate_ans == "":
            for chunk in spacy_nlp_sent.noun_chunks:
                candidate_ans +=" "+ str(chunk.text)
            
    if que_type=="num":
        for token in spacy_nlp_sent:
            if token.lemma_ == root_word:
                for cand in [child for child in token.children]:
                    if check_num(cand.ent_type_):
                        candidate_ans +=" "+ str(cand.text)
                        for c in cand.children:
                            if check_num(cand.ent_type_):
                                candidate_ans +=" "+ str(c.text)
                    elif cand.dep_ == "prep":
                        candidate_ans += " "+ find_answer(spacy_nlp_sent, cand, "", que_type)
                    elif cand.dep_ == "nummod":
                        for chunk in spacy_nlp_sent.noun_chunks:
                            if chunk.root.text == cand.text:
                                candidate_ans +=" "+ str(chunk.text)
        if candidate_ans == "":
            for token in spacy_nlp_sent.ents:
                if check_where(token.label_):
                    candidate_ans += " "+str(token.text)
        if candidate_ans == "":
            for chunk in spacy_nlp_sent.noun_chunks:
                candidate_ans +=" "+ str(chunk.text)
    
    if que_type=="desc":
        candidate_ans = ""

        if candidate_ans == "":
            for chunk in spacy_nlp_sent:
                if chunk.pos_ == 'NOUN' or chunk.pos_ == 'PROPN':
                    candidate_ans +=" "+ str(chunk.text)
                    
    if que_type=="binary":
        for chunk in spacy_nlp_sent:
            if chunk.pos_ == 'NOUN' or chunk.pos_ == 'PROPN':
                candidate_ans +=" "+ str(chunk.text)

    final_answer = ""
    
    
    if not candidate_ans:
        for chunk in spacy_nlp_sent:
            if chunk.pos_ == 'NOUN' or chunk.pos_ == 'PROPN':
                candidate_ans +=" "+ str(chunk.text)
    
    candidate_ans = candidate_ans.split()
    candidate_ans = " ".join(set(candidate_ans))
    
    question_token = [token.text for token in spacy_nlp(question)]
    for token in spacy_nlp(candidate_ans):
        if token.text not in question_token:
            final_answer += " "+str(token.text)
    final_answer = final_answer.split()
    final_answer = " ".join(set([w for w in final_answer if w not in stopwords.words('english') and w != "="]))

    return final_answer


In [9]:
def formalize(text):
    ans = re.sub(r' ,', ',', text)
    ans = re.sub(r' %', '%', ans)
    ans = re.sub(r'\( ', '(', ans)
    ans = re.sub(r' \)', ')', ans)
    ans = re.sub(r'\$ ', '$', ans)
    ans = re.sub(r' \.', '.', ans)
    ans = re.sub(r' ’', "’", ans)
    ans = re.sub(r" \'", "'", ans)
    ans = re.sub(r" !", "!", ans)
    ans = re.sub(r" :", ":", ans)
    ans = re.sub(r"\[ ", "[", ans)
    ans = re.sub(r" \]", "]", ans)
    ans = re.sub(r'`` ', '"', ans)
    ans = re.sub(r" \'\'", '"', ans)
    ans = re.sub(r"\'\'", '"', ans)
    ans = re.sub(r' \$', '$', ans)
    ans = re.sub(r' -', '-', ans)
    ans = re.sub(r'# ', '#', ans)
    return ans

In [12]:
from functools import partial
import csv


with open('some.csv', 'w', newline='', encoding='utf-8') as csv_fp:
        csv_fp_writer = csv.writer(csv_fp, delimiter=',')
        csv_fp_writer.writerow(["id", "answer"])
        csv_fp.close()


with open('out.csv', 'w', newline='', encoding='utf-8') as csv_fp1:
        csv_fp_writer1 = csv.writer(csv_fp1, delimiter=',')
        csv_fp_writer1.writerow(["id", "root", "sentence"])
        csv_fp1.close()


test = json.load(open("testing.json", 'r'))


def check_que_type(class_que):
    if class_que in when_type:
        return "when"
    if class_que in where_type:
        return "where"
    if class_que in who_type:
        return "who"
    if class_que in num_type:
        return "num"
    else:
        return "desc"

for iteration in tqdm(range(3618)):
    question = test[iteration].get('question')
    
    wh_trigram = question_type(question)
    
    doc_id = test[iteration].get('docid')
    query_vect = convert_query_vect([question], vect[doc_id])

    sentence_id = rank_sent(tfidf[doc_id], convert_query_vect([question], vect[doc_id]))
    
    final_answer = ""
    sen_candidate = ''
    for sen_id in sentence_id:
        final_answer = extract_answer(question, wh_trigram[2], sent[doc_id][sen_id], query_type(wh_trigram))
        if not final_answer:
            continue
        else:
            sen_candidate = sent[doc_id][sen_id]
            break

    final_answer = final_answer.split()
    final_answer = " ".join(set(final_answer))

    with open('some.csv', 'a', newline='') as csv_fp2:
            csv_fp_writer2 = csv.writer(csv_fp2)
            csv_fp_writer2.writerow([iteration, final_answer])

    with open('out.csv', 'a', newline='') as csv_fp3:
            csv_fp_writer3 = csv.writer(csv_fp3)
            csv_fp_writer3.writerow([iteration,wh_trigram[2], sen_candidate])

csv_fp2.close()
csv_fp3.close()

  0%|          | 2/3618 [00:00<04:32, 13.28it/s]

4444444444444444444444
5555555555555555555555555
888888888888888888888888
['what', 'defacto', 'base']
what
defacto
-------
desc
00000000000
desc type
none found yet
00000000000000000000000000000000000000
 web browsers combination standards HTML XHTML way browsers
standards combination way XHTML HTML web browsers
------------
Modern browser support standards-based and defacto what?
below is final answer
combination way XHTML web HTML browsers
above is final answer
4444444444444444444444
5555555555555555555555555
7777777777777777777
['what', 'people', 'typically']
what
people
-------
who
00000000000
who type
These
components
achieve
different
functionalities
of
a
web
browser
and
together
provide
all
capabilities
of
a
web
browser
.
none found yet
00000000000000000000000000000000000000
 These components different functionalities a web browser all capabilities a web browser
different components a all capabilities browser functionalities web These
------------
What do people typically call a

  0%|          | 3/3618 [00:02<51:28,  1.17it/s]

22222222222222222222222
What is it called when content is changed from markup to an interactive document?
5555555555555555555555555
7777777777777777777
['what', 'call', 'when']
what
call
-------
desc
00000000000
desc type
none found yet
00000000000000000000000000000000000000
 HTML content image files information CSS browser engine markup document process
content image browser document engine markup CSS process HTML information files
------------
What is it called when content is changed from markup to an interactive document?
below is final answer
image browser engine CSS process HTML information files
above is final answer
4444444444444444444444
5555555555555555555555555
7777777777777777777
['what', 'platform', 'browser']
what
platform
-------
desc
00000000000
desc type
none found yet
00000000000000000000000000000000000000
 Internet Explorer Mac
Internet Explorer Mac
------------
What platform is a browser used on?
below is final answer
Internet Explorer Mac
above is final answer
4444

  0%|          | 7/3618 [00:02<24:40,  2.44it/s]

...

4444444444444444444444
5555555555555555555555555
7777777777777777777
['which', 'number', 'rank']
-------
num
00000000000
num type
During
the
Song
dynasty
(
906–1279
)
,
officials
of
the
top
three
ranks
ranks
-----below line is children for ranks
the 
-----below line is children for ranks
top 
-----below line is children for ranks
three CARDINAL
three CARDINAL
wore
purple
clothes
;
those
of
the
fourth
and
fifth
wore
bright
red
;
those
of
the
sixth
and
seventh
wore
green
;
and
the
eighth
and
ninth
wore
blue
.
00000000000000000000000000000000000000
 three
three
------------
Which number of ranks wore purple clothing in the Song dynasty?
below is final answer
three
above is final answer
4444444444444444444444
5555555555555555555555555
7777777777777777777
['what', 'year', 'nation']
what
year
+++++++++=
-------
when
00000000000
when type
Red
is
the
international
color
of
stop
signs
and
stop
lights
on
highways
and
intersections
.
<class 'str'>
none found yet
0000000000000000000000000000000000

100%|█████████▉| 3616/3618 [07:21<00:00,  8.19it/s]

4444444444444444444444
5555555555555555555555555
7777777777777777777
['what', 'year', 'community']
what
year
+++++++++=
-------
when
00000000000
when type
Today
the
Communist
Party
of
China
claims
to
be
the
largest
political
party
in
the
world
,
with
eighty
million
members
.
<class 'str'>
none found yet
the Communist Party of China ORG
eighty million CARDINAL
00000000000000000000000000000000000000
 the Communist Party China the largest political party the world eighty million members
the world eighty China million political largest party members Party Communist
------------
In what year was the Community Party of China created?
below is final answer
world Communist million political largest party members eighty
above is final answer
4444444444444444444444
5555555555555555555555555
7777777777777777777
['what', 'turkey', 'red']
what
turkey
-------
desc
00000000000
desc type
none found yet
00000000000000000000000000000000000000
 color Europe Turkey India century Turkey red France rouge d'

100%|██████████| 3618/3618 [07:21<00:00,  8.19it/s]

5555555555555555555555555
7777777777777777777
['what', 'pigment', 'turkey']
what
pigment
-------
desc
00000000000
desc type
none found yet
00000000000000000000000000000000000000
 color Europe Turkey India century Turkey red France rouge d'Adrinople
Turkey rouge century Europe red color France India d'Adrinople
------------
What other pigment was Turkey red compared to?
below is final answer
rouge century Europe color France India d'Adrinople
above is final answer
